In [1]:
import numpy as np
import time
from numpy.random import uniform

## List approach (so slow)

In [155]:
uncertainty_dict = {}
uncertainty_list = []
x_range = np.arange(-5,5.1,0.1)
y_range = np.arange(-5,5.1,0.1)
z_range = np.arange(0,5.1,0.1)

N = len(x_range)
for i in range(len(x_range)):
    for j in range(len(y_range)):
        for k in range(len(z_range)):
            element = (x_range[i], y_range[j], z_range[k])
            uncertainty_dict[element] = 1
            uncertainty_list.append([x_range[i], y_range[j], z_range[k]])
        
uncertainty_grids = np.array(uncertainty_list)
uncertainty_values = np.ones((uncertainty_grids.shape[0], ))

In [44]:
dist = 1e6
eps = 0.25
current_pos = [1.0, 2.0, 3.5]
closest_grid = None

for key, value in uncertainty_list.items():
    current_dist = np.sqrt((key[0]-current_pos[0])**2 + (key[1]-current_pos[1])**2 + (key[2]-current_pos[2])**2)
    if current_dist < dist:
        dist = current_dist
        closest_grid = key
        
    if current_dist <= eps:
        print ("that's right")
        break
        
closest_grid

that's right


(1.0, 2.0, 3.5)

## Array approach (much faster)

In [9]:
x_lim, y_lim, z_lim = 20, 20, 6
eps = 0.1
res = 1
X,Y,Z = np.mgrid[-x_lim:x_lim+eps:res, -y_lim:y_lim+eps:res, 0:z_lim+eps:res*2]
uncertainty_grids = np.vstack((X.flatten(), Y.flatten(), Z.flatten())).T
uncertainty_values = np.ones((uncertainty_grids.shape[0], ))
grid_visits = np.zeros((uncertainty_grids.shape[0], ))

print (uncertainty_grids.shape)
print (np.sqrt(uncertainty_grids.shape[0]))

(6724, 3)
82.0


In [8]:
uncertainty_grids[0]

array([-20., -20.,   0.])

In [11]:
current_pos = [1.75, 2.0, 3.5]

differences = current_pos-uncertainty_grids
distances = np.sum(differences*differences,axis=1)
min_ind = np.argmin(distances)
print("Closest grid: ",uncertainty_grids[min_ind])
print("Uncertainty value: ", uncertainty_values[min_ind])

# Closest N grids
dist = 5.0
indices = np.where(distances<dist)[0]
print ("Closest N Grids: ", len(indices))

Closest grid:  [2. 2. 4.]
Uncertainty value:  1.0
Closest N Grids:  25


In [72]:
def closest_grid(current_pos):
    differences = current_pos-uncertainty_grids
    distances = np.sum(differences*differences,axis=1)
    min_ind = np.argmin(distances)
    
    return min_ind

In [12]:
uncertainty_values[distances<dist] = 0.3

grid_visits[distances<dist] += 1

In [57]:
np.clip(np.exp(-grid_visits[distances<dist]), 1e-6, 1.0)

array([0.36787944, 0.36787944, 0.36787944, 0.36787944, 0.36787944,
       0.36787944, 0.36787944, 0.36787944, 0.36787944, 0.36787944,
       0.36787944, 0.36787944, 0.36787944, 0.36787944, 0.36787944,
       0.36787944, 0.36787944, 0.36787944, 0.36787944, 0.36787944,
       0.36787944, 0.36787944, 0.36787944, 0.36787944, 0.36787944,
       0.36787944, 0.36787944, 0.36787944, 0.36787944, 0.36787944,
       0.36787944, 0.36787944, 0.36787944, 0.36787944, 0.36787944,
       0.36787944, 0.36787944, 0.36787944, 0.36787944, 0.36787944,
       0.36787944, 0.36787944, 0.36787944, 0.36787944, 0.36787944,
       0.36787944, 0.36787944, 0.36787944, 0.36787944, 0.36787944])

In [89]:
drone_pos_stack = np.zeros(uncertainty_values.shape)
drone_pos_stack[min_ind] = 1
drone_pos_stack = drone_pos_stack.reshape(82,82)

grid_xyz_0 = np.array([uniform(-10, 10), uniform(-10, 10), uniform(0.5,3)])
grid_xyz_1 = grid_xyz_0 + np.array([uniform(0, 5), uniform(0, 5), uniform(0.5,3)])

print (grid_xyz_0)
print (grid_xyz_1)

print (closest_grid(grid_xyz_0))
print (closest_grid(grid_xyz_1))

[ 9.89994975 -6.88315257  2.92694057]
[12.84574727 -2.41378293  4.2853012 ]
4973
5486


In [90]:
x_range = np.arange(grid_xyz_0[0], grid_xyz_1[0], 0.25)
y_range = np.arange(grid_xyz_0[1], grid_xyz_1[1], 0.25)
z_range = np.arange(grid_xyz_0[2], grid_xyz_1[2], 0.5)

indices = []
for x in x_range:
    for y in y_range:
        for z in z_range:
            current_pos = np.array([x,y,z])
            current_ind = closest_grid(current_pos)
            if current_ind not in indices:
                indices.append(current_ind)

# Read Agents' Positions

In [2]:
import pickle

In [20]:
with open('agents_positions.pkl', 'rb') as f:
    total_pos_list = pickle.load(f)

In [21]:
for episode in range(len(total_pos_list)):
    episode_pos_list = total_pos_list[episode]
    for agent_ind in range(len(episode_pos_list)):
        for iteration in range(len(episode_pos_list[agent_ind])):
            agent_pos = episode_pos_list[agent_ind][iteration]
            print ("Episode {4}, Agent {0} X:{1:.4}, Y:{2:.4}, Z:{3:.4}".format(agent_ind+1, agent_pos[0], agent_pos[1], agent_pos[2], episode+1))

Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0
Episode 1, Agent 1 X:6.0, Y:12.0, Z:4.0


Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0

Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0, Z:2.5
Episode 1, Agent 1 X:-12.0, Y:-7.0

Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent

Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent 2 X:9.0, Y:-15.0, Z:2.0
Episode 1, Agent

...

Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0

Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0, Z:4.0
Episode 8, Agent 1 X:11.0, Y:-19.0

Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0

Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0

Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0, Z:4.0
Episode 8, Agent 2 X:-9.0, Y:-18.0